In [149]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os
import unicodedata as uni
import numpy as np
from nltk.stem import PorterStemmer
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import wordnet
import math
import pprint

pp=pprint.PrettyPrinter(indent=4)

# Naive Approach

* read in table

In [2]:
table = pd.read_csv('../Tools/emoji_descriptions.csv')
table.head()

Unnamed: 0    code character               description  Unnamed: 4
0           0  126980         🀄   MAHJONG TILE RED DRAGON         NaN
1           1  129525         🧵           SPOOL OF THREAD         NaN
2           2  129526         🧶              BALL OF YARN         NaN
3           3  127183         🃏  PLAYING CARD BLACK JOKER         NaN
4           4  129296         🤐         ZIPPER-MOUTH FACE         NaN

* todo: read in a lot of messages

In [3]:
messages = ["Hello, this is a testing message", "this is a very sunny day today, i am very happy"]

In [4]:
ps = PorterStemmer()

In [5]:
stemmed_messages = []
for m in messages:
    words = word_tokenize(m)
    sm = []
    for w in words:
        sm.append(ps.stem(w))
    stemmed_messages.append(sm)

In [6]:
stemmed_messages

[['hello', ',', 'thi', 'is', 'a', 'test', 'messag'],
 ['thi',
  'is',
  'a',
  'veri',
  'sunni',
  'day',
  'today',
  ',',
  'i',
  'am',
  'veri',
  'happi']]

In [7]:
table.shape

(1027, 5)

* compare words to emoji descriptions

In [59]:
def evaluate_sentence(sentence):
    tokenized_sentence = word_tokenize(sentence)
    n = len(tokenized_sentence)
    l = table.shape[0]
    matrix_list = []
    
    for index, row in table.iterrows():
        emoji_tokens = word_tokenize(row['description'])
        m = len(emoji_tokens)

        mat = np.zeros(shape=(m,n))
        for i in range(len(emoji_tokens)):
            for j in range(len(tokenized_sentence)):
                syn1 = wordnet.synsets(emoji_tokens[i])
                if len(syn1) == 0:
                    continue
                w1 = syn1[0]
                #print(j, tokenized_sentence)
                syn2 = wordnet.synsets(tokenized_sentence[j])
                if len(syn2) == 0:
                    continue
                w2 = syn2[0]
                val = w1.wup_similarity(w2)
                if val is None:
                    continue
                mat[i,j] = val
        #print(row['character'], mat)
        matrix_list.append(mat)
            
    return matrix_list
    
    

In [177]:
result = evaluate_sentence("horse back riding")

* building a lookup table:

In [178]:
lookup = {}
emoji_set = []
for index, row in table.iterrows():
    lookup[index] = row['character']
    emoji_set.append(row['character'])

emoji_set = set(emoji_set)

* sorting

In [179]:
summed = np.argsort([-np.sum(x) for x in result])
max_val = np.argsort([-np.max(x) for x in result])
avg =  np.argsort([-np.mean(x) for x in result])

t = 0.9
threshold = np.argsort([-len(np.where(x>t)[0]) / (x.shape[0] * x.shape[1]) for x in result])


In [180]:
def print_best_results(sorted_indices, n=10):
    pp.pprint([lookup[x] + " -- " + str(table.iloc[x]['description']) for x in sorted_indices[:10]])
    pp.pprint([result[x] for x in sorted_indices[:10]])

In [181]:
print_best_results(threshold)

[   '🐎 -- HORSE',
    '🏇 -- HORSE RACING',
    '🐴 -- HORSE FACE',
    '\U0001f993 -- ZEBRA FACE',
    '🏅 -- SPORTS MEDAL',
    '🗻 -- MOUNT FUJI',
    '🎠 -- CAROUSEL HORSE',
    '🤚 -- RAISED BACK OF HAND',
    '🔙 -- BACK WITH LEFTWARDS ARROW ABOVE',
    '📮 -- POSTBOX']
[   array([[1.        , 0.19047619, 0.08333333]]),
    array([[1.        , 0.19047619, 0.08333333],
       [0.08333333, 0.13333333, 0.88888889]]),
    array([[1.        , 0.19047619, 0.08333333],
       [0.18181818, 0.76923077, 0.125     ]]),
    array([[0.93333333, 0.19047619, 0.08333333],
       [0.18181818, 0.76923077, 0.125     ]]),
    array([[0.08695652, 0.14285714, 0.94117647],
       [0.09090909, 0.15384615, 0.25      ]]),
    array([[0.96774194, 0.18181818, 0.08      ],
       [0.4       , 0.19047619, 0.08333333]]),
    array([[0.07407407, 0.11111111, 0.19047619],
       [1.        , 0.19047619, 0.08333333]]),
    array([[0.1       , 0.18181818, 0.14285714],
       [0.19047619, 1.        , 0.13333333],
       [0.